In [ ]:
import pandas as pd
import numpy as np
from glove import Corpus
from nltk import pos_tag
import gensim
from gensim.models import Word2Vec
import re
from nltk.corpus import wordnet as wn
# from textgenrnn import textgenrnn
import os
import nltk
import warnings
import pickle
warnings.filterwarnings('ignore')
import sys
nltk.download('averaged_perceptron_tagger')
data="/content/imdb_dataset.csv"
itr="1"
fold=1
label=8
loc_save = "/content/sample_data/augdata"
z=open(data,"r")
len1=len(z.readlines())-1
len2=int(len1/fold)
#Writing into file
df=pd.DataFrame()
def writing_into_file(aug_temp,target_path,y,x):
    print(aug_temp,"pppooooooooooo")
    str1=""
    g1=open(target_path,"a")
    for i in range(label):
        str1=str1+y[i]
        g1.write(y[i])
        g1.write(" ")
    df['sentiment']=str1
    g1.write("\t")
    df['review']=x
    g1.write(x)
    g1.write("\n")
    for i in range(1,len(aug_temp)):
        str2=""
        for j in range(label):
            str2=str2+y[j]
            g1.write(y[j])
            g1.write(" ")
        
        g1.write("\t")
        g1.write(aug_temp[i])
        g1.write("\n")

class Augment():
    def __init__(self,
                 method,
                 source_path,
                 target_path,
                 corpus_='none',
                 valid_tags=['NN'],
                 threshold=0.20,
                 x_col='review',
                 y_col='sentiment'):
        f=[]
        df = pd.read_csv(source_path, encoding = "ISO-8859-1")
        review=df['review'].tolist()
        sentiment = df['sentiment'].tolist()
        dbfile = open('google_bin.pickle', 'ab') 
        pickle.dump(review, dbfile)                      
        dbfile.close() 
         #self.model = get_corpus(corpus_)
        self.sentences = pickle.load(open("google_bin.pickle","rb"))
        review_text=df.review.apply(gensim.utils.simple_preprocess
                            )
        self.model=gensim.models.Word2Vec(min_count=1)
        self.model.build_vocab(review_text)
        self.model.train(review_text,total_examples=self.model.corpus_count,epochs=5)
        # self.model=Word2Vec(self.sentences, min_count=1)

        print('Loaded corpus: ', corpus_)
        self.x_col=x_col
        self.y_col=y_col

        self.df=pd.read_csv(source_path)
        self.augmented=pd.DataFrame(columns=[x_col, y_col])
        self.method=method
        self.valid_tags = valid_tags
        self.threshold_ = threshold
        g1=open(target_path,'a')
        # Go through each row in dataframe
        
        if method != 'generate':
            count=0
            f=[]
            count1=-1
            
            for idx, row in self.df.iterrows():
                count1+=1
            
                if count1>=(int(itr)-1)*len2 and count1<(int(itr))*len2:
                    
                    try:
                        if count%200==0:
                            print("Counter :",count)
                        count+=1
       
                        x = self.preprocess(row[self.x_col])
                        
                        pre=row[self.x_col]
                        
                        
                        y = row[self.y_col].zfill(label)
                       
                        if method =='postag':
                            aug_temp = self.postag(x)
                            
                            writing_into_file(aug_temp,target_path,y,pre)
                            
                        if method =='threshold':
                        
                            aug_temp = self.threshold(x)
                            writing_into_file(aug_temp,target_path,y,pre)
                          
    
                            
                    except:
                        pass

                
                else:
                    pass

        else:
            self.generate('hate', 100)


    def preprocess(self, x):
        x = re.sub("[^a-zA-Z ]+", "", x)
        x = x.split()
        return x

    def postag(self, x):
        n = 0
        dict = {}
        
        tags = pos_tag(x)
        # print(x,"pppppp")
        for idx, word in enumerate(x):
            # print(word,"party")
            # print(idx,word,"2222222222222222222222")
            if tags[idx][1] in self.valid_tags and word in self.model.wv.vocab:
                # print(tags[idx][1],self.valid_tags,"11111")
                replacements = self.model.wv.most_similar(positive=word, topn=2)
                # print(replacements,word,"ooo")
                replacements = [elem[0] for elem in replacements]
                # print(replacements,word,"1111111111111111")
                dict.update({word:replacements})
                n = len(replacements) if len(replacements) > n else n
        return self.create_augmented_samples(dict, n, x)

    def create_augmented_samples(self, dict, n, x):
        aug_tweets = [x]
        for i in range(n):
            single_augment = x[:]
            for idx, word in enumerate(single_augment):
                if word in dict.keys() and len(dict[word]) >= i+1:
                    single_augment[idx] = dict[word][i]
            single_augment = ' '.join(single_augment)
            aug_tweets.append(single_augment)
            # print(aug_tweets,"ffffffffffff")
        # print(aug_tweets)
        return aug_tweets


    def threshold(self, x):
        dict = {}
        n = 0
        tags = pos_tag(x)
        # print(x)
        for idx, word in enumerate(x):
            # print(word,"uuu")
            if word in self.model.wv.vocab:
                #get words with highest cosine similarity
                # print(word,"iiiii")
                replacements = self.model.wv.most_similar(positive=word, topn=1)
                #keep only words that pass the threshold
                # print(replacements,"uuuuuu")
                replacements = [replacements[i][0] for i in range(1) if replacements[i][1] > self.threshold_]
                #check for POS tag equality, dismiss if unequal
                # print(replacements)
                replacements = [elem for elem in replacements if pos_tag([elem.lower()])[0][1] == tags[idx][1]]
                print(replacements,word,"ttttt")
                dict.update({word:replacements}) if len(replacements) > 0 else dict
                n = len(replacements) if len(replacements) > n else n
                break
        return self.create_augmented_samples(dict, n, x)


#     def EDA(self, class_, n_, to_file=False):
#         
#         df_class = self.df[self.df[y_col] == class_]
#         class_path = 'class_filter.csv'
#         df_class.to_csv(class_path) #write temporary csv file to train RNN instance
#         textgen = textgenrnn(name=self.method)
#         textgen.train_from_file(
#             file_path=class_path,
#             num_epochs=10,
#             batch_size=128,
#             new_model=True,
#             word_level=True
#         )

#         #generate new samples
#         if to_file:
#             textgen.generate_to_file(self.target, n=n_, temperature=1.0)
#         else: #will print to screen
#             textgen.generate(n_, temperature=1.0)

#         #clean up repo
#         os.remove(class_path)
#         os.remove(self.method+'_config.json')
#         os.remove(self.method+'vocab.json')
#         os.remove(self.method+'_weights.hdf5')




#Augmenting using pos method 
if __name__ == '__main__':
    
    Augment('threshold', data, str(loc_save)+'/augmented_data_nlp_1_'+str(itr)+'.csv', 'google')
    print(df)

[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
Loaded corpus:  google
Counter : 0
[['One', 'of', 'the', 'other', 'reviewers', 'has', 'mentioned', 'that', 'after', 'watching', 'just', 'Oz', 'episode', 'youll', 'be', 'hooked', 'They', 'are', 'right', 'as', 'this', 'is', 'exactly', 'what', 'happened', 'with', 'mebr', 'br', 'The', 'first', 'thing', 'that', 'struck', 'me', 'about', 'Oz', 'was', 'its', 'brutality', 'and', 'unflinching', 'scenes', 'of', 'violence', 'which', 'set', 'in', 'right', 'from', 'the', 'word', 'GO', 'Trust', 'me', 'this', 'is', 'not', 'a', 'show', 'for', 'the', 'faint', 'hearted', 'or', 'timid', 'This', 'show', 'pulls', 'no', 'punches', 'with', 'regards', 'to', 'drugs', 'sex', 'or', 'violence', 'Its', 'is', 'hardcore', 'in', 'the', 'classic', 'use', 'of', 'the', 'wordbr', 'br', 'It', 'is', 'called', 'OZ', 'as', 'that', 'is', 'the

In [ ]:
def f1(df):
  print(df)

In [ ]:
data="/content/dataset.csv"
loc_save="/content/sample_data/augdata"


In [ ]:
df

NameError: ignored

In [ ]:
! pip install glove-python-binary

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 948 kB 25.9 MB/s 


In [ ]:
!pip list

Package                       Version
----------------------------- ---------------------
absl-py                       1.0.0
alabaster                     0.7.12
albumentations                0.1.12
altair                        4.2.0
appdirs                       1.4.4
argon2-cffi                   21.3.0
argon2-cffi-bindings          21.2.0
arviz                         0.11.4
astor                         0.8.1
astropy                       4.3.1
astunparse                    1.6.3
atari-py                      0.2.9
atomicwrites                  1.4.0
attrs                         21.4.0
audioread                     2.1.9
autograd                      1.3
Babel                         2.9.1
backcall                      0.2.0
beautifulsoup4                4.6.3
bleach                        4.1.0
blis                          0.4.1
bokeh                         2.3.3
Bottleneck                    1.3.4
branca                        0.4.2
bs4                           0.0.1
CacheC

In [ ]:
!pip install nlpaug
!pip install nltk
!pip install wordnet

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 410 kB 22.6 MB/s 
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Created wheel for wordnet: filename=wordnet-0.0.1b2-py3-none-any.whl size=10521 sha256=6223e805f3f62392c3ad868d3073cfae114b8eaa27ef763850347bc71adfdfab
  Stored in directory: /root/.cache/pip/wheels/8c/6d/01/fbf1762cd6428569ea48474660f9cfe029307cd6c0f2abcdec
Successfully built wordnet


In [ ]:
import pandas as pd
import nlpaug.augmenter.word as naw
df=pd.read_csv("/content/imdb_dataset.csv")
aug = naw.AntonymAug(name='Antonym_Aug', aug_min=1, aug_max=10, aug_p=0.3, lang='eng', stopwords=None, tokenizer=None, 
                     reverse_tokenizer=None, stopwords_regex=None, verbose=0)
# test_sentence= aug.augment("I love to spend most of the time in gardening")

for i in range(len(df)):
  df['review'][i] = aug.augment(df['review'][i])
  df['sentiment'][i] = df['sentiment'][i]
df.to_excel("imdb_antonym.xlsx")
# test_sentence

In [ ]:
df['review'][0]
# df=pd.read_csv("/content/imdb_dataset.csv")
# for i in range(len(df)):
#   print(df["review"][i],end='\n\n\n\n\n')

"i of the honest to god perceiver detainment founder reference that after insure aside all unity and on the galvanising seal battery window window assault and battery lucy in the sky with diamonds Oz chronological chronological chronological ecological succession you ' ll monetary gossiper scrimp economical clock prison house sign status promissory banker ' s greenback execration delete out back 4th attribute sparring notation value hint. They indue upwards by respectable frugal economical financial aid oneself hand sizeable heart and psyche, as this live but what bulge out with pine sir herbert sir william henry maxmilian beerbohm tree sir superior victor victor herbert sir henry maxmilian beerbohm sir herbert beerbohm sir victor herbert beerbohm tree diagram sir lord superior towering stride achiever victor overlord passe partout eminent rank herbert sir nuclear bit nonpareil maxmilian goop sir henry maxmilian sir william henry maxmilian beerbohm sir winner herbert gentle ballad sir 

In [ ]:
df.to_excel("antonymdataset.xlsx")

In [ ]:
import nltk
nltk.download('wordnet')

[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Unzipping corpora/wordnet.zip.


True

In [ ]:
import nltk

nltk.download('averaged_perceptron_tagger')

[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Unzipping taggers/averaged_perceptron_tagger.zip.


True

In [ ]:
df

Empty DataFrame
Columns: []
Index: []